In [1]:
from PIL import Image
 
# Convert encoding data into 8-bit binary
# form using ASCII value of characters
def genData(data):
 
        # list of binary codes
        # of given data
        newd = []
 
        for i in data:
            newd.append(format(ord(i), '08b'))
        return newd
 
# Pixels are modified according to the
# 8-bit binary data and finally returned
def modPix(pix, data):
 
    datalist = genData(data)
    lendata = len(datalist)
    imdata = iter(pix)
 
    for i in range(lendata):
 
        # Extracting 3 pixels at a time
        pix = [value for value in imdata.__next__()[:3] +
                                imdata.__next__()[:3] +
                                imdata.__next__()[:3]]
 
        # Pixel value should be made
        # odd for 1 and even for 0
        for j in range(0, 8):
            if (datalist[i][j] == '0' and pix[j]% 2 != 0):
                pix[j] -= 1
 
            elif (datalist[i][j] == '1' and pix[j] % 2 == 0):
                if(pix[j] != 0):
                    pix[j] -= 1
                else:
                    pix[j] += 1
                # pix[j] -= 1
 
        # Eighth pixel of every set tells
        # whether to stop ot read further.
        # 0 means keep reading; 1 means thec
        # message is over.
        if (i == lendata - 1):
            if (pix[-1] % 2 == 0):
                if(pix[-1] != 0):
                    pix[-1] -= 1
                else:
                    pix[-1] += 1
 
        else:
            if (pix[-1] % 2 != 0):
                pix[-1] -= 1
 
        pix = tuple(pix)
        yield pix[0:3]
        yield pix[3:6]
        yield pix[6:9]
 
def encode_enc(newimg, data):
    w = newimg.size[0]
    (x, y) = (0, 0)
 
    for pixel in modPix(newimg.getdata(), data):
 
        # Putting modified pixels in the new image
        newimg.putpixel((x, y), pixel)
        if (x == w - 1):
            x = 0
            y += 1
        else:
            x += 1
 
# Encode data into image
def encode():
    img = input("Enter image name(with extension) : ")
    image = Image.open(img, 'r')
 
    data = input("Enter data to be encoded : ")
    if (len(data) == 0):
        raise ValueError('Data is empty')
 
    newimg = image.copy()
    encode_enc(newimg, data)
 
    new_img_name = input("Enter the name of new image(with extension) : ")
    newimg.save(new_img_name, str(new_img_name.split(".")[1].upper()))
 
# Decode the data in the image
def decode():
    img = input("Enter image name(with extension) : ")
    image = Image.open(img, 'r')
 
    data = ''
    imgdata = iter(image.getdata())
 
    while (True):
        pixels = [value for value in imgdata.__next__()[:3] +
                                imgdata.__next__()[:3] +
                                imgdata.__next__()[:3]]
 
        # string of binary data
        binstr = ''
 
        for i in pixels[:8]:
            if (i % 2 == 0):
                binstr += '0'
            else:
                binstr += '1'
 
        data += chr(int(binstr, 2))
        if (pixels[-1] % 2 != 0):
            return data
 
# Main Function
def main():
    a = int(input(":: Welcome to Steganography ::\n"
                        "1. Encode\n2. Decode\n"))
    if (a == 1):
        encode()
 
    elif (a == 2):
        print("Decoded Word :  " + decode())
    else:
        raise Exception("Enter correct input")
 


In [7]:
main()

:: Welcome to Steganography ::
1. Encode
2. Decode
1
Enter image name(with extension) : pika.jpeg
Enter data to be encoded : bob
Enter the name of new image(with extension) : pika-enc.jpeg


In [11]:
main()

:: Welcome to Steganography ::
1. Encode
2. Decode
2
Enter image name(with extension) : pika-enc.jpeg
Decoded Word :  ÿ


In [12]:
#Lets try another kind (Image in Image)

In [22]:
import cv2
import numpy as np
import random
  
  
# Encryption function
def encrypt():
      
    # img1 and img2 are the
    # two input images
    img1 = cv2.imread('pic1.jpg')
    img2 = cv2.imread('pic2.jpg')
      
    for i in range(img2.shape[0]):
        for j in range(img2.shape[1]):
            for l in range(3):
                  
                # v1 and v2 are 8-bit pixel values
                # of img1 and img2 respectively
                v1 = format(img1[i][j][l], '08b')
                print("v1 for ", i,j,l)
                print(v1)
                print(v1[:4])
                v2 = format(img2[i][j][l], '08b')
                print("v2 for ", i,j,l)
                print(v2)
                print(v2[:4])  
                # Taking 4 MSBs of each image
                v3 = v1[:4] + v2[:4]
                print("v3 for ", i,j,l)
                print(v3)
                  
                img1[i][j][l]= int(v3, 2)
                  
    cv2.imwrite('pic3in2.png', img1)
  
      
# Decryption function
def decrypt():
      
    # Encrypted image
    img = cv2.imread('pic3in2.png') 
    width = img.shape[0]
    height = img.shape[1]
      
    # img1 and img2 are two blank images
    img1 = np.zeros((width, height, 3), np.uint8)
    img2 = np.zeros((width, height, 3), np.uint8)
      
    for i in range(width):
        for j in range(height):
            for l in range(3):
                v1 = format(img[i][j][l], '08b')
                v2 = v1[:4] + chr(random.randint(0, 1)+48) * 4
                v3 = v1[4:] + chr(random.randint(0, 1)+48) * 4
                  
                # Appending data to img1 and img2
                img1[i][j][l]= int(v2, 2)
                img2[i][j][l]= int(v3, 2)
      
    # These are two images produced from
    # the encrypted image
    cv2.imwrite('pic2_re.png', img1)
    cv2.imwrite('pic3_re.png', img2)
      

In [23]:
encrypt()

v1 for  0 0 0
11110011
1111
v2 for  0 0 0
00000000
0000
v3 for  0 0 0
11110000
v1 for  0 0 1
11111001
1111
v2 for  0 0 1
01000011
0100
v3 for  0 0 1
11110100
v1 for  0 0 2
11111000
1111
v2 for  0 0 2
01101000
0110
v3 for  0 0 2
11110110
v1 for  0 1 0
11111010
1111
v2 for  0 1 0
00100011
0010
v3 for  0 1 0
11110010
v1 for  0 1 1
11111111
1111
v2 for  0 1 1
01101101
0110
v3 for  0 1 1
11110110
v1 for  0 1 2
11111111
1111
v2 for  0 1 2
10010001
1001
v3 for  0 1 2
11111001
v1 for  0 2 0
11110001
1111
v2 for  0 2 0
00100111
0010
v3 for  0 2 0
11110010
v1 for  0 2 1
11111010
1111
v2 for  0 2 1
01111000
0111
v3 for  0 2 1
11110111
v1 for  0 2 2
11111101
1111
v2 for  0 2 2
10011101
1001
v3 for  0 2 2
11111001
v1 for  0 3 0
11101011
1110
v2 for  0 3 0
00100101
0010
v3 for  0 3 0
11100010
v1 for  0 3 1
11110100
1111
v2 for  0 3 1
01111101
0111
v3 for  0 3 1
11110111
v1 for  0 3 2
11111000
1111
v2 for  0 3 2
10100001
1010
v3 for  0 3 2
11111010
v1 for  0 4 0
11111000
1111
v2 for  0 4 0
00100110
0

v2 for  0 40 0
01100100
0110
v3 for  0 40 0
11110110
v1 for  0 40 1
11111101
1111
v2 for  0 40 1
10000011
1000
v3 for  0 40 1
11111000
v1 for  0 40 2
11111101
1111
v2 for  0 40 2
10110000
1011
v3 for  0 40 2
11111011
v1 for  0 41 0
11111101
1111
v2 for  0 41 0
10111101
1011
v3 for  0 41 0
11111011
v1 for  0 41 1
11111101
1111
v2 for  0 41 1
11100011
1110
v3 for  0 41 1
11111110
v1 for  0 41 2
11111101
1111
v2 for  0 41 2
11111111
1111
v3 for  0 41 2
11111111
v1 for  0 42 0
11111101
1111
v2 for  0 42 0
01100110
0110
v3 for  0 42 0
11110110
v1 for  0 42 1
11111101
1111
v2 for  0 42 1
10000001
1000
v3 for  0 42 1
11111000
v1 for  0 42 2
11111101
1111
v2 for  0 42 2
10011100
1001
v3 for  0 42 2
11111001
v1 for  0 43 0
11111101
1111
v2 for  0 43 0
10010011
1001
v3 for  0 43 0
11111001
v1 for  0 43 1
11111101
1111
v2 for  0 43 1
10101000
1010
v3 for  0 43 1
11111010
v1 for  0 43 2
11111101
1111
v2 for  0 43 2
10111101
1011
v3 for  0 43 2
11111011
v1 for  0 44 0
11111101
1111
v2 for  0 44 0
1

11111000
v1 for  0 79 1
11111101
1111
v2 for  0 79 1
01111001
0111
v3 for  0 79 1
11110111
v1 for  0 79 2
11111101
1111
v2 for  0 79 2
01111111
0111
v3 for  0 79 2
11110111
v1 for  0 80 0
11111101
1111
v2 for  0 80 0
10000110
1000
v3 for  0 80 0
11111000
v1 for  0 80 1
11111101
1111
v2 for  0 80 1
01110111
0111
v3 for  0 80 1
11110111
v1 for  0 80 2
11111101
1111
v2 for  0 80 2
01111111
0111
v3 for  0 80 2
11110111
v1 for  0 81 0
11111101
1111
v2 for  0 81 0
10000000
1000
v3 for  0 81 0
11111000
v1 for  0 81 1
11111101
1111
v2 for  0 81 1
01110011
0111
v3 for  0 81 1
11110111
v1 for  0 81 2
11111101
1111
v2 for  0 81 2
01111011
0111
v3 for  0 81 2
11110111
v1 for  0 82 0
11111101
1111
v2 for  0 82 0
10000110
1000
v3 for  0 82 0
11111000
v1 for  0 82 1
11111101
1111
v2 for  0 82 1
01110110
0111
v3 for  0 82 1
11110111
v1 for  0 82 2
11111101
1111
v2 for  0 82 2
01111101
0111
v3 for  0 82 2
11110111
v1 for  0 83 0
11111101
1111
v2 for  0 83 0
10000011
1000
v3 for  0 83 0
11111000
v1 for 

v2 for  0 118 1
00010111
0001
v3 for  0 118 1
11110001
v1 for  0 118 2
11111101
1111
v2 for  0 118 2
00011000
0001
v3 for  0 118 2
11110001
v1 for  0 119 0
11111101
1111
v2 for  0 119 0
01000010
0100
v3 for  0 119 0
11110100
v1 for  0 119 1
11111101
1111
v2 for  0 119 1
00100010
0010
v3 for  0 119 1
11110010
v1 for  0 119 2
11111101
1111
v2 for  0 119 2
00100011
0010
v3 for  0 119 2
11110010
v1 for  0 120 0
11111101
1111
v2 for  0 120 0
01001101
0100
v3 for  0 120 0
11110100
v1 for  0 120 1
11111101
1111
v2 for  0 120 1
00101100
0010
v3 for  0 120 1
11110010
v1 for  0 120 2
11111101
1111
v2 for  0 120 2
00110000
0011
v3 for  0 120 2
11110011
v1 for  0 121 0
11111101
1111
v2 for  0 121 0
01010000
0101
v3 for  0 121 0
11110101
v1 for  0 121 1
11111101
1111
v2 for  0 121 1
00110000
0011
v3 for  0 121 1
11110011
v1 for  0 121 2
11111101
1111
v2 for  0 121 2
00110101
0011
v3 for  0 121 2
11110011
v1 for  0 122 0
11111101
1111
v2 for  0 122 0
01001111
0100
v3 for  0 122 0
11110100
v1 for  0 

v1 for  0 157 2
11111101
1111
v2 for  0 157 2
01000001
0100
v3 for  0 157 2
11110100
v1 for  0 158 0
11111101
1111
v2 for  0 158 0
01001111
0100
v3 for  0 158 0
11110100
v1 for  0 158 1
11111101
1111
v2 for  0 158 1
00110101
0011
v3 for  0 158 1
11110011
v1 for  0 158 2
11111101
1111
v2 for  0 158 2
01000011
0100
v3 for  0 158 2
11110100
v1 for  0 159 0
11111101
1111
v2 for  0 159 0
01010001
0101
v3 for  0 159 0
11110101
v1 for  0 159 1
11111101
1111
v2 for  0 159 1
00110111
0011
v3 for  0 159 1
11110011
v1 for  0 159 2
11111101
1111
v2 for  0 159 2
01000101
0100
v3 for  0 159 2
11110100
v1 for  0 160 0
11111010
1111
v2 for  0 160 0
01010101
0101
v3 for  0 160 0
11110101
v1 for  0 160 1
11111011
1111
v2 for  0 160 1
00111011
0011
v3 for  0 160 1
11110011
v1 for  0 160 2
11111111
1111
v2 for  0 160 2
01001001
0100
v3 for  0 160 2
11110100
v1 for  0 161 0
11111011
1111
v2 for  0 161 0
01010011
0101
v3 for  0 161 0
11110101
v1 for  0 161 1
11111101
1111
v2 for  0 161 1
00111001
0011
v3 fo

...

v2 for  25 417 0
01110000
0111
v3 for  25 417 0
11100111
v1 for  25 417 1
11110001
1111
v2 for  25 417 1
01100100
0110
v3 for  25 417 1
11110110
v1 for  25 417 2
11110001
1111
v2 for  25 417 2
01111010
0111
v3 for  25 417 2
11110111
v1 for  25 418 0
11110001
1111
v2 for  25 418 0
01111000
0111
v3 for  25 418 0
11110111
v1 for  25 418 1
11110011
1111
v2 for  25 418 1
01101011
0110
v3 for  25 418 1
11110110
v1 for  25 418 2
11110011
1111
v2 for  25 418 2
10000011
1000
v3 for  25 418 2
11111000
v1 for  25 419 0
11110111
1111
v2 for  25 419 0
01111110
0111
v3 for  25 419 0
11110111
v1 for  25 419 1
11111001
1111
v2 for  25 419 1
01110001
0111
v3 for  25 419 1
11110111
v1 for  25 419 2
11111001
1111
v2 for  25 419 2
10001001
1000
v3 for  25 419 2
11111000
v1 for  25 420 0
11111001
1111
v2 for  25 420 0
01111110
0111
v3 for  25 420 0
11110111
v1 for  25 420 1
11111011
1111
v2 for  25 420 1
01110010
0111
v3 for  25 420 1
11110111
v1 for  25 420 2
11111011
1111
v2 for  25 420 2
10001000
1000
v

11111000
1111
v2 for  25 448 1
01111000
0111
v3 for  25 448 1
11110111
v1 for  25 448 2
11111001
1111
v2 for  25 448 2
10000100
1000
v3 for  25 448 2
11111000
v1 for  25 449 0
11110110
1111
v2 for  25 449 0
10000001
1000
v3 for  25 449 0
11111000
v1 for  25 449 1
11111000
1111
v2 for  25 449 1
01110101
0111
v3 for  25 449 1
11110111
v1 for  25 449 2
11111001
1111
v2 for  25 449 2
10000001
1000
v3 for  25 449 2
11111000
v1 for  25 450 0
11110110
1111
v2 for  25 450 0
01110001
0111
v3 for  25 450 0
11110111
v1 for  25 450 1
11111000
1111
v2 for  25 450 1
01100110
0110
v3 for  25 450 1
11110110
v1 for  25 450 2
11111001
1111
v2 for  25 450 2
01110110
0111
v3 for  25 450 2
11110111
v1 for  25 451 0
11110110
1111
v2 for  25 451 0
01000001
0100
v3 for  25 451 0
11110100
v1 for  25 451 1
11111000
1111
v2 for  25 451 1
00111010
0011
v3 for  25 451 1
11110011
v1 for  25 451 2
11111001
1111
v2 for  25 451 2
01001001
0100
v3 for  25 451 2
11110100
v1 for  25 452 0
11110110
1111
v2 for  25 452 0
0

v3 for  25 487 1
11111110
v1 for  25 487 2
11111011
1111
v2 for  25 487 2
11111111
1111
v3 for  25 487 2
11111111
v1 for  25 488 0
11110011
1111
v2 for  25 488 0
10100000
1010
v3 for  25 488 0
11111010
v1 for  25 488 1
11110100
1111
v2 for  25 488 1
11010110
1101
v3 for  25 488 1
11111101
v1 for  25 488 2
11111000
1111
v2 for  25 488 2
11110111
1111
v3 for  25 488 2
11111111
v1 for  25 489 0
11110111
1111
v2 for  25 489 0
10011111
1001
v3 for  25 489 0
11111001
v1 for  25 489 1
11111001
1111
v2 for  25 489 1
11011000
1101
v3 for  25 489 1
11111101
v1 for  25 489 2
11111010
1111
v2 for  25 489 2
11111000
1111
v3 for  25 489 2
11111111
v1 for  25 490 0
11110101
1111
v2 for  25 490 0
10011011
1001
v3 for  25 490 0
11111001
v1 for  25 490 1
11110111
1111
v2 for  25 490 1
11010101
1101
v3 for  25 490 1
11111101
v1 for  25 490 2
11111000
1111
v2 for  25 490 2
11111001
1111
v3 for  25 490 2
11111111
v1 for  25 491 0
11110010
1111
v2 for  25 491 0
10010000
1001
v3 for  25 491 0
11111001
v1 for

1011
v2 for  26 26 2
01110111
0111
v3 for  26 26 2
10110111
v1 for  26 27 0
11111010
1111
v2 for  26 27 0
00000000
0000
v3 for  26 27 0
11110000
v1 for  26 27 1
11111100
1111
v2 for  26 27 1
00000001
0000
v3 for  26 27 1
11110000
v1 for  26 27 2
11111111
1111
v2 for  26 27 2
01011010
0101
v3 for  26 27 2
11110101
v1 for  26 28 0
11110010
1111
v2 for  26 28 0
00000010
0000
v3 for  26 28 0
11110000
v1 for  26 28 1
11110011
1111
v2 for  26 28 1
00000001
0000
v3 for  26 28 1
11110000
v1 for  26 28 2
11111101
1111
v2 for  26 28 2
01100001
0110
v3 for  26 28 2
11110110
v1 for  26 29 0
11101111
1110
v2 for  26 29 0
00001000
0000
v3 for  26 29 0
11100000
v1 for  26 29 1
11110010
1111
v2 for  26 29 1
00000010
0000
v3 for  26 29 1
11110000
v1 for  26 29 2
11110110
1111
v2 for  26 29 2
01100111
0110
v3 for  26 29 2
11110110
v1 for  26 30 0
11111000
1111
v2 for  26 30 0
00010000
0001
v3 for  26 30 0
11110001
v1 for  26 30 1
11111101
1111
v2 for  26 30 1
00000011
0000
v3 for  26 30 1
11110000
v1 fo

KeyboardInterrupt: 

In [17]:
decrypt()

In [24]:
from pynq.overlays.base import BaseOverlay

base = BaseOverlay('base.bit')

In [28]:
%%microblaze base.PMODA
int add(int a, int b){
    return a+b;
}

In [27]:
add(4,6)

10

In [3]:
%%microblaze base.PMODA
int add(array[][][] a){
    return a;
}

UsageError: Cell magic `%%microblaze` not found.
